-----------Structure dashboard music---------------------------

- Count of songs per year/month/dow/dom/hod
- Listening time per day/week/month
- Ranking of artists, genre, album per year, trends over the year (or per period of time, possibility to select to/from date)
- Count aggregation per week or month
- Comparison of songs listened to vs when they were released
- Life cycle of a song (listened to for a long period, vs short period)
- Songs, genre liked/disliked 
- Variation calculation with previous year/month/week stats
- Genre depending on the moment of the year/week/day
- Main device used to listen to Apple Music
- Total minutes played and a comparison with how much time it represents in my life

In [1]:
#import statements

import pandas as pd
import numpy as np
import math
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from difflib import SequenceMatcher


In [2]:
#import dataset

#optional - recent activity
#recent_containers_df = pd.read_csv("data/Apple_Media_Services/Apple Music Activity/Apple Music - Recently Played Containers.csv")
#recent_tracks_df = pd.read_csv('data/Apple_Media_Services/Apple Music Activity/Apple Music - Recently Played Tracks.csv')

#songs played activity
play_activity_df =pd.read_csv('data/Apple_Media_Services/Apple Music Activity/Apple Music Play Activity.csv')

#songs liked and disliked
likes_dislikes_df = pd.read_csv('data/Apple_Media_Services/Apple Music Activity/Apple Music Likes and Dislikes.csv')

#correspondance between track Id and track detailed info
library_tracks_info_df = pd.read_json("data/Apple_Media_Services/Apple Music Activity/Apple Music Library Tracks.json")

#general activity on Apple Music, including play activity
library_activity_df = pd.read_json("data/Apple_Media_Services/Apple Music Activity/Apple Music Library Activity.json")

#identifer info
identifier_infos_df = pd.read_json("data/Apple_Media_Services/Apple Music Activity/Identifier Information.json")



In [3]:
print("Shape of the play activity df: ", play_activity_df.shape)

Shape of the play activity df:  (25402, 31)


In [4]:
print("Shape of the likes/dislikes df: ", likes_dislikes_df.shape)

Shape of the likes/dislikes df:  (444, 5)


In [5]:
print("Shape of the app activity df: ", library_activity_df.shape)

Shape of the app activity df:  (1213, 19)


In [6]:
print("Shape of the list of songs with their id: ", identifier_infos_df.shape)

Shape of the list of songs with their id:  (695, 2)


So basically, the dataframe that contains most of the information, is the play activity df (well, that makes sense !).
A total of 444 songs were flagged (liked/disliked).
It is not crystal clear what the library activity dataframe contains, so let's take a closer look at it!

## Analyzing the activity in the application

* What are the types of "transactions" performed in the library?
* From what device is it most often done?
* Can we visualize a timeline of the activity?

In [7]:
library_activity_df['Transaction Type'].value_counts()

updateItems              639
addItems                 330
updateContainer          141
appendContainerItems      55
deleteItems               25
addContainers              5
deleteContainer            4
updateUser                 4
addContainer               4
subscribeToPlaylist        2
updateItem                 2
optInUser                  1
replaceContainerItems      1
Name: Transaction Type, dtype: int64

In [8]:
#focus on the updateItems, that seems to be the one occurring more often

library_activity_df[library_activity_df['Transaction Type'] == 'updateItems']

Transaction Type  Transaction Identifier      Transaction Date  \
5         updateItems                10000007  2016-07-08T17:30:57Z   
21        updateItems                10000023  2016-07-12T06:07:48Z   
31        updateItems                10000033  2016-07-12T06:11:02Z   
34        updateItems                10000037  2016-07-13T00:08:13Z   
38        updateItems                10000041  2016-07-20T03:56:07Z   
...               ...                     ...                   ...   
1207      updateItems                10001246  2020-04-20T04:00:06Z   
1208      updateItems                10001247  2020-04-20T04:44:05Z   
1209      updateItems                10001248  2020-04-20T05:18:07Z   
1211      updateItems                10001250  2020-04-25T01:54:57Z   
1212      updateItems                10001251  2020-04-25T03:51:52Z   

                                              UserAgent  \
5                                     Internal Software   
21    itunescloudd/1.0 iOS/9.3.2 model/iPhone6,2 hwp...   
31    itunescloudd/1.0 iOS/9.3.2 model/iPhone6,2 hwp...   
34    itunescloudd/1.0 iOS/9.3.2 model/iPhone6,2 hwp...   
38    itunescloudd/1.0 iOS/9.3.2 model/iPhone6,2 hwp...   
...                                                 ...   
1207                                  Internal Software   
1208                                  Internal Software   
1209                                  Internal Software   
1211                                  Internal Software   
1212                                  Internal Software   

     Subscription Start Date Subscription Type  \
5                        NaN               NaN   
21                       NaN               NaN   
31                       NaN               NaN   
34                       NaN               NaN   
38                       NaN               NaN   
...                      ...               ...   
1207                     NaN               NaN   
1208                     NaN               NaN   
1209                     NaN               NaN   
1211                     NaN               NaN   
1212                     NaN               NaN   

                                                 Tracks User Playlists  \
5     [{'Track Identifier': 182857742, 'Apple Music ...  NaN       NaN   
21    [{'Track Identifier': 182857758, 'Date Added T...  NaN       NaN   
31    [{'Track Identifier': 182858018, 'Last Played ...  NaN       NaN   
34    [{'Track Identifier': 182857986, 'Last Played ...  NaN       NaN   
38    [{'Track Identifier': 182857782, 'Last Played ...  NaN       NaN   
...                                                 ...  ...       ...   
1207  [{'Track Identifier': 182873122, 'Track Like R...  NaN       NaN   
1208  [{'Track Identifier': 182873118, 'Tag Matched ...  NaN       NaN   
1209  [{'Track Identifier': 182873122, 'Tag Matched ...  NaN       NaN   
1211  [{'Track Identifier': 182873126, 'Track Like R...  NaN       NaN   
1212  [{'Track Identifier': 182873126, 'Tag Matched ...  NaN       NaN   

     Country Language Playlist Track Identifiers  Playlist Identifier  \
5        NaN      NaN      NaN               NaN                  NaN   
21       FRA    fr-fr      NaN               NaN                  NaN   
31       FRA    fr-fr      NaN               NaN                  NaN   
34       FRA    fr-fr      NaN               NaN                  NaN   
38       FRA    fr-fr      NaN               NaN                  NaN   
...      ...      ...      ...               ...                  ...   
1207     FRA    fr-fr      NaN               NaN                  NaN   
1208     FRA    fr-fr      NaN               NaN                  NaN   
1209     FRA    fr-fr      NaN               NaN                  NaN   
1211     FRA    fr-fr      NaN               NaN                  NaN   
1212     FRA    fr-fr      NaN               NaN                  NaN   

     Playlist Track Identifiers Track Playlist Item Identifiers Appended  \


In [9]:
# We see that the Tracks column contains an array of dictionaries, let's look at it in more details

library_activity_df[library_activity_df['Transaction Type'] == 'updateItems']['Tracks'].iloc[20]

[{'Track Identifier': 182858774, 'Last Played Date': '2016-08-02T00:18:54Z'}]

In this case we see that the Last Played Date of the song is updated. Is this information available elsewhere? Let's take a look at the track info details

In [10]:
library_tracks_info_df.columns

Index(['Content Type', 'Track Identifier', 'Title', 'Sort Name', 'Artist',
       'Sort Artist', 'Is Part of Compilation', 'Album', 'Sort Album',
       'Album Artist', 'Genre', 'Track Year', 'Track Number On Album',
       'Track Count On Album', 'Disc Number Of Album', 'Disc Count Of Album',
       'Track Duration', 'Track Play Count', 'Date Added To Library',
       'Date Added To iCloud Music Library', 'Last Modified Date',
       'Purchase Date', 'Skip Count', 'Is Purchased', 'Audio File Extension',
       'Is Checked', 'Release Date', 'Purchased Track Identifier',
       'Audio Matched Track Identifier', 'Date of Last Skip', 'Grouping',
       'Comments', 'Beats Per Minute', 'Last Played Date', 'Rating',
       'Album Rating', 'Remember Playback Position', 'Album Like Rating',
       'Track Like Rating', 'Album Rating Method', 'Work Name',
       'Movement Name', 'Movement Number', 'Movement Count',
       'Display Work Name', 'Apple Music Track Identifier', 'Composer',
       'C

We see that there is indeed a 'Last Played Date' info available.

So it looks like this dataframe keeps track of any modification that occured in the library, such as:
- whether a song was added to the library, or to a playlist, 
- whether a playlist was created
- last played date
- ...


By the way, we see that there are two identifiers used to identify the tracks in both app_activity_df and tracks_info_df. 
**We will use Track Identifier further on to refer to a song**

We also notice that there is a column containing UserAgent. Let's take a closer look at the information it contains.

In [11]:
library_activity_df['UserAgent'].value_counts()

Internal Software                                                                              90
itunescloudd/1.0 iOS/12.1 model/iPhone11,8 hwp/t8020 build/16B93 (6; dt:194)                   62
itunescloudd/1.0 iOS/9.3.2 model/iPhone6,2 hwp/s5l8960x build/13F69 (6; dt:90)                 60
itunescloudd/1.0 iOS/11.4.1 model/iPhone6,2 hwp/s5l8960x build/15G77 (6; dt:90)                60
AMPLibraryAgent/1.0.3 (Macintosh; OS X 10.15.3) AppleWebKit/608.5.11 build/1 (dt:1)            59
itunescloudd/1.0 iOS/10.2.1 model/iPhone6,2 hwp/s5l8960x build/14D27 (6; dt:90)                48
itunescloudd/1.0 iOS/11.3 model/iPhone8,4 hwp/s8003 build/15E216 (6; dt:129)                   43
itunescloudd/1.0 iOS/11.1.2 model/iPhone6,2 hwp/s5l8960x build/15B202 (6; dt:90)               41
itunescloudd/1.0 iOS/10.3.2 model/iPhone6,2 hwp/s5l8960x build/14F89 (6; dt:90)                39
itunescloudd/1.0 iOS/12.0 model/iPhone6,2 hwp/s5l8960x build/16A366 (6; dt:90)                 36
itunescloudd/1.0 iOS

There are four main categories :
- Internal Software
- AMPLibraryAgent
- iTunes (from a Macintosh)
- itunescloudd (from an iPhone)

Let's create two new columns to be able to do some filtering on the data later : 
- transaction year, to see trends during the years
- transaction month, to see trends during the months
- transaction day of the week, to see trends during the day of the week
- transaction agent, to identfy from where the action was performed

In [12]:
# we add columns to extract year, month, day of the month and day of the week from the transaction date

library_activity_df['Transaction Simplified Date'] = pd.to_datetime(library_activity_df['Transaction Date'].str.split('T').str.get(0))
library_activity_df['Transaction Year'] = library_activity_df['Transaction Date'].str.split('-').str.get(0)
library_activity_df['Transaction Month'] = library_activity_df['Transaction Date'].str.split('-').str.get(1)
library_activity_df['Transaction DOW'] = library_activity_df['Transaction Simplified Date'].dt.day_name()
library_activity_df['Transaction Agent'] = library_activity_df['UserAgent'].str.split('/').str.get(0)


In [13]:
# simplifying the values of the transaction agent

library_activity_df['Transaction Agent'] = library_activity_df['Transaction Agent'].replace(to_replace ="itunescloudd", value ="iPhone")
library_activity_df['Transaction Agent'] = library_activity_df['Transaction Agent'].replace(to_replace ="iTunes", value ="Macintosh")


In [14]:
# plotting the distribution of action per date and agent

color = {'Internal Software':'rgb(149, 216, 64)', 'AMPLibraryAgent':'rgb(68, 1, 84)',
         'iPhone':'rgb(220, 227, 25)', 'Macintosh':'rgb(45, 112, 142)'}


graph = []


graph.append(
    go.Scatter(
        name='iPhone',
        x=library_activity_df[library_activity_df['Transaction Agent'] == 'iPhone']['Transaction Simplified Date'],
        y=library_activity_df[library_activity_df['Transaction Agent'] == 'iPhone']['Transaction Type'],
        showlegend=True,
        mode='markers',
        marker=dict(
            size=math.log(library_activity_df[library_activity_df['Transaction Agent'] == 'iPhone']['Transaction Type'].count()*1000),
            color=color['iPhone'],
            opacity=0.2,
        ),
    ))
graph.append(
    go.Scatter(
        name='AMPLibraryAgent',
        x=library_activity_df[library_activity_df['Transaction Agent'] == 'AMPLibraryAgent']['Transaction Simplified Date'],
        y=library_activity_df[library_activity_df['Transaction Agent'] == 'AMPLibraryAgent']['Transaction Type'],
        showlegend=True,
        mode='markers',
        marker=dict(
            size=math.log(library_activity_df[library_activity_df['Transaction Agent'] == 'AMPLibraryAgent']['Transaction Type'].count()*1000),
            color=color['AMPLibraryAgent'],
            opacity=0.5,
        ),
    ))
graph.append(
    go.Scatter(
        name='Internal Software',
        x=library_activity_df[library_activity_df['Transaction Agent'] == 'Internal Software']['Transaction Simplified Date'],
        y=library_activity_df[library_activity_df['Transaction Agent'] == 'Internal Software']['Transaction Type'],
        showlegend=True,
        mode='markers',
        marker=dict(
            size=math.log(library_activity_df[library_activity_df['Transaction Agent'] == 'Internal Software']['Transaction Type'].count()*1000),
            color=color['Internal Software'],
            opacity=0.5,
        ),
    ))
graph.append(
    go.Scatter(
        name='Macintosh',
        x=library_activity_df[library_activity_df['Transaction Agent'] == 'Macintosh']['Transaction Simplified Date'],
        y=library_activity_df[library_activity_df['Transaction Agent'] == 'Macintosh']['Transaction Type'],
        showlegend=True,
        mode='markers',
        marker=dict(
            size=math.log(library_activity_df[library_activity_df['Transaction Agent'] == 'Macintosh']['Transaction Type'].count()*1000),
            color=color['Macintosh'],
            opacity=0.8,
        ),
    )
)


layout = dict(title='Number of transaction per date and agent',
                  yaxis=dict(title="Transaction type"),
                  xaxis=dict(title="Date"))

fig = go.Figure(data=graph, layout=layout)
fig.show()


Some insights already on the data:
- AMPLibraryAgent started being active in 2020 -> available from MacOS Catalina (late 2019, possible update made in Jan, 2020)
- the platform most used is apparently the iPhone
- there are two periods where Internal Software was most active : oct2017-feb2018 and 2020

Let's simplify this graph to visualize only the platforms used (knowing that the model of the iPhone has changed several times since 2016!)


In [15]:
library_activity_df['Transaction Agent Model'] = library_activity_df[library_activity_df['Transaction Agent'] == 'iPhone']['UserAgent'].str.split('/').str.get(3).str.split(',').str.get(0)
library_activity_df.loc[library_activity_df['Transaction Agent'].eq('Macintosh'), 'Transaction Agent Model'] = 'Macintosh'


In [16]:
library_activity_df['Transaction Agent Model'].unique()[1:]

array(['iPhone6', 'iPad4', 'Macintosh', 'iPhone8', 'iPhone11'],
      dtype=object)

In [17]:
#plotting the repartition of operations per device

labels = library_activity_df['Transaction Agent Model'].unique()[1:]
values = library_activity_df['Transaction Agent Model'].value_counts()

fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
fig.show()

## Analyzing the play activity

In [18]:
play_activity_df.iloc[120]

Apple Id Number                                                           456135196
Apple Music Subscription                                                       True
Artist Name                                                    Clamavi De Profundis
Build Version                     Music/3.1 iOS/12.0.1 model/iPhone6,2 hwp/s5l89...
Client IP Address                                                    213.173.165.23
Content Name                                       Lamentations of Jeremiah 2:12-15
Content Provider                                                      TuneCore, Inc
Content Specific Type                                                          Song
Device Identifier                          64226df8f71b0671d2ea6ce1fc4e745ce1f62b41
End Position In Milliseconds                                                 227787
End Reason Type                                                NATURAL_END_OF_TRACK
Event End Timestamp                                        2018-11-12T12:13:

Just at first glance, there are many columns that look very interesting:
- Event Type / End Reason Type -> to spot whether a track was skipped
- Feature Name -> to spot how the track was found (ex: suggestion playlist)
- Genre
- Content Name/Artist Name -> to be able to fetch info about the track
- Event Start Timestamp -> to identify when the track was listened to

We also notice that this df does not contain any column with an id that can help us match each row to some information contained in the other df....

In [19]:
play_activity_df['Event Type'].unique()

array(['PLAY_END', 'PLAY_START', 'LYRIC_DISPLAY'], dtype=object)

In [20]:
play_activity_df['End Reason Type'].unique()

array(['NOT_APPLICABLE', 'NATURAL_END_OF_TRACK', 'TRACK_SKIPPED_FORWARDS',
       'PLAYBACK_MANUALLY_PAUSED', 'SCRUB_BEGIN',
       'MANUALLY_SELECTED_PLAYBACK_OF_A_DIFF_ITEM', 'FAILED_TO_LOAD',
       'SCRUB_END', nan, 'TRACK_SKIPPED_BACKWARDS'], dtype=object)

So for any given song, we can use Event Type PLAY_START to identify when the song was played.
Then using End Reason Type we can identify :
- whether a song was skipped or partially listened to (TRACK_SKIPPED_BACKWARDS and TRACK_SKIPPED_FORWARDS, and SCRUB_BEGIN)
- listened to entirely (NATURAL_END_OF_TRACK)

For now we will leave aside the LYRIC_DISPLAY, but it is good to know it is available!

Also note that whenever we see End Reason Type == NOT_APPLICABLE, we can assume that is is because a track that is not available in iTunes was played? We will agglomerate all these rows into an 'other' category for the analysis.

In [21]:
play_activity_df['Feature Name'].unique()

array([nan, 'search / playlist_detail', 'library / playlist_detail',
       'for_you', 'library / songs',
       'for_you / recently_played / album_detail',
       'for_you / playlist_detail', 'search',
       'for_you / recently_played / playlist_detail',
       'for_you / days_playlist / playlist_detail',
       'for_you / personalized_mix / playlist_detail',
       'search / album_detail', 'search / add-to-upnext',
       'for_you / artist_playlist / playlist_detail', 'my-music',
       'for_you / personalized_mix', 'for_you:none / product',
       'library / album_detail', 'library / downloaded_music / songs',
       'library / artist_detail / album_detail', 'browse',
       'for_you:none / for-you', 'Siri-actions-local', 'library',
       'library / album_detail / artist_detail / artist_see_all',
       'music_stack/pinned', 'search:none / search',
       'search / artist_detail / artist_see_all', 'siri', 'library/songs',
       'now_playing', 'new',
       'library / downloaded_m

We can use this column to filter the 'origin' of the song, but to simplify we will stick to four categories:
- for_you, sub-divided into three main categories
    - personalized_mix
    - recently_played
    - other suggestions (friends_listening, days_playlist, artist_playlist)
- search + browse
- library
- other
    

## Building a dataframe for visualization - Feature construction

### Focus on the play activity

Let's create some new columns, and actually keep only those that we are interested in for the analysis.
For a start, we can get read of the following columns:
- Apple Id Number
- Apple Music Subscription
- Build Version
- Client IP Address
- Device Identifier
- Event Reason Hint Type
- Event Received Timestamp
- Media Type
- Metrics Bucket Id
- Metrics Client Id
- Milliseconds Since Play
- Source Type
- Store Country Name

In [22]:
columns_to_drop = [
    'Apple Id Number', 'Apple Music Subscription', 'Build Version', 'Client IP Address',
    'Content Specific Type', 'Device Identifier', 'Event Reason Hint Type',
    'End Position In Milliseconds', 'Event Received Timestamp', 'Media Type', 'Metrics Bucket Id', 
    'Metrics Client Id','Original Title', 'Source Type', 'Start Position In Milliseconds',
    'Store Country Name', 'Milliseconds Since Play'
]

df_analysis = play_activity_df.drop(columns_to_drop, axis=1)


In [23]:
df_analysis

Artist Name                                    Content Name  \
0                    NaN                                             NaN   
1                    NaN                                             NaN   
2                    NaN                                             NaN   
3                    NaN                                             NaN   
4      How to Dress Well  World I Need You, Won't Be Without You (Proem)   
...                  ...                                             ...   
25397       Klaus Badelt                                   One Last Shot   
25398        Cosmic Baby                               Movements In Love   
25399   Lindsey Stirling                    Shatter Me (feat. Lzzy Hale)   
25400  Antti Martikainen                                       Legendary   
25401            Ricoune                         On a le web à la maison   

                    Content Provider           End Reason Type  \
0                                NaN            NOT_APPLICABLE   
1                                NaN            NOT_APPLICABLE   
2                                NaN            NOT_APPLICABLE   
3                                NaN            NOT_APPLICABLE   
4          Domino Recording Co. Ltd.      NATURAL_END_OF_TRACK   
...                              ...                       ...   
25397                     UMG Global  PLAYBACK_MANUALLY_PAUSED   
25398          Kontor New Media GmbH      NATURAL_END_OF_TRACK   
25399  Universal Music International  PLAYBACK_MANUALLY_PAUSED   
25400           PK Interactive, Inc.      NATURAL_END_OF_TRACK   
25401                  TuneCore, Inc      NATURAL_END_OF_TRACK   

            Event End Timestamp     Event Start Timestamp Event Type  \
0      2018-04-09T14:15:29.569Z  2018-04-09T14:11:10.613Z   PLAY_END   
1      2018-04-09T12:43:10.943Z  2018-04-09T12:39:02.454Z   PLAY_END   
2      2018-01-02T14:39:32.297Z  2018-01-02T14:39:29.744Z   PLAY_END   
3      2016-12-02T07:22:43.761Z  2016-12-02T07:22:34.766Z   PLAY_END   
4      2018-01-07T10:37:02.275Z  2018-01-07T10:34:13.327Z   PLAY_END   
...                         ...                       ...        ...   
25397  2016-08-16T08:03:25.899Z  2016-08-16T08:01:27.899Z   PLAY_END   
25398  2017-11-02T14:18:25.120Z  2017-11-02T14:09:34.498Z   PLAY_END   
25399  2018-09-25T09:17:00.796Z  2018-09-25T09:16:41.844Z   PLAY_END   
25400  2018-11-21T15:47:56.196Z  2018-11-21T15:44:40.824Z   PLAY_END   
25401  2018-01-22T09:50:11.762Z  2018-01-22T09:46:34.284Z   PLAY_END   

                                 Feature Name              Genre  \
0                                         NaN                NaN   
1                                         NaN                NaN   
2                                         NaN                NaN   
3                                         NaN                NaN   
4                    search / playlist_detail        Alternative   
...                                       ...                ...   
25397                                     NaN         Soundtrack   
25398                                 for_you         Electronic   
25399                                     NaN                Pop   
25400  library / artist_detail / album_detail         Soundtrack   
25401               library / playlist_detail  Singer/Songwriter   

                             Item Type  Media Duration In Milliseconds  \
0      AGGREGATE_NON_CATALOG_PLAY_TIME                        151092.0   
1      AGGREGATE_NON_CATALOG_PLAY_TIME                        248084.0   
2      AGGREGATE_NON_CATALOG_PLAY_TIME                          1261.0   
3      AGGREGATE_NON_CATALOG_PLAY_TIME                          8222.0   
4                 ITUNES_STORE_CONTENT                        168948.0   
...                                ...                             ...   
25397             ITUNES_STORE_CONTENT                        286000.0   
25398             ITUNES_STORE_CO

Let's add columns to 
1. extract year, month, day of month, day of week and hour of the day of the playing activity, using as a reference the moment the 'Event Start Timestamp', and when not available using 'Event End Timestamp'
2. track the 'origin' of the song (i.e. how it was found) ; qualify the song as external to Apple Music as 'other'
3. whether the song was skipped/listened to partially
4. the duration of the listening activity


In [24]:
# Rename columns for merges later

df_analysis = df_analysis.rename(columns={'Content Name':'Title',
                          'Artist Name':'Artist'})
        

In [25]:
# Add time related columns

# Define reference activity time column
df_analysis['Activity date time'] = pd.to_datetime(df_analysis['Event Start Timestamp'])
df_analysis['Activity date time'].fillna(pd.to_datetime(df_analysis['Event End Timestamp']), inplace=True)

# Add broken down date into year, month, day of the month, day of the week
df_analysis['Play Year']=df_analysis['Activity date time'].dt.year
df_analysis['Play Month']=df_analysis['Activity date time'].dt.month
df_analysis['Play DOM']=df_analysis['Activity date time'].dt.day
df_analysis['Play DOW']=df_analysis['Activity date time'].dt.day_name()

# Add hour of the day in UTC and in local time

df_analysis['Play HOD UTC']=df_analysis['Activity date time'].dt.hour
df_analysis['Play HOD Local Time']=df_analysis['Play HOD UTC'] + df_analysis['UTC Offset In Seconds']/3600
df_analysis['Play HOD Local Time'] = df_analysis['Play HOD Local Time'].astype(int)

In [26]:
# Add partial listening column

def set_partial_listening(df):
    if df['End Reason Type'] == 'NATURAL_END_OF_TRACK':
        return True
    else:
        #if the play duration is above the media duration, we consider the track to be listened to completely
        if df['Play Duration Milliseconds'] >= df['Media Duration In Milliseconds']:
            return True
        else:
            return False

df_analysis['Played completely'] = df_analysis.apply(set_partial_listening, axis=1)


In [27]:
# Add track origin column

def get_track_origin(x):
    if str(x) != 'nan':
        x_cat = str(x).split('/')[0].strip()
        if x_cat == 'search' or x_cat =='browse':
            return 'search'
        elif x_cat == 'library' or x_cat == 'my-music' or x_cat == 'playlists' or x_cat == 'playlist_detail':
            return 'library'
        elif x_cat == 'for_you':
            if len(str(x).split('/')) > 1:
                x_subcat = str(x).split('/')[1].strip()
                if x_subcat == 'recently_played':
                    return 'for you - recently played'
                elif x_subcat == 'personalized_mix':
                    return 'for you - personalized mix'
                else:
                    return 'for you - other'
            else:
                return 'for you - other'
        else:
            return 'other'
    else:
        return 'other'
    

# we add a column with the origin of the song, and remove the column Feature Name
df_analysis['Track origin'] = df_analysis['Feature Name'].apply(get_track_origin)
df_analysis = df_analysis.drop(['Feature Name'], axis=1)


In [28]:
# Add play duration column

def compute_play_duration(df):
    end = pd.to_datetime(df['Event End Timestamp'])
    start = pd.to_datetime(df['Event Start Timestamp'])
    if str(end) != 'NaT' and str(start) != 'NaT':
        if end.day == start.day:
            diff = end - start
            duration = diff.total_seconds()/60
        else:
            duration = df['Media Duration In Milliseconds']/60000
    else:
        if df['Played completely'] is False:
            if type(df['Play Duration Milliseconds']) == float:
                duration = df['Media Duration In Milliseconds']/60000
            else:
                duration = df['Play Duration Milliseconds']/60000       
        else:
            duration = df['Media Duration In Milliseconds']/60000
    return duration

df_analysis['Play duration in minutes'] = df_analysis.apply(compute_play_duration, axis=1)

# we remove outliers from this column, saying that if a value if above the 99th percentile,
# we drop it, and replace it by the duration of the media

def remove_outliers(df):
    if df['Play duration in minutes'] <= percentile:
        return df['Play duration in minutes']
    else:
        return df['Media Duration In Milliseconds']/60000



percentile = df_analysis['Play duration in minutes'].quantile(0.99)
df_analysis['Play duration in minutes'] = df_analysis.apply(remove_outliers, axis=1)


#we can then remove the columns we do not need anymore!
df_analysis = df_analysis.drop(['Event End Timestamp', 'Event Start Timestamp', 'UTC Offset In Seconds',
                                'Play Duration Milliseconds', 'Media Duration In Milliseconds'], axis=1)


### Building a data structure for tracks

What would be ideal, would be to also track whether the song is in the library, and whether if it was liked/disliked. This information comes from two other df, so we need a way to match the rows with items from likes_dislikes_df and library_tracks_info_df. 

Let's build up separate objects to ease our job of matching items from these df.

In [29]:
# function to measure the similarity between two strings (usegful to match titles in particular)

def similar(a, b):
    return SequenceMatcher(None, a, b).ratio()

In [30]:
# This class is going to help us building a reference data structure for all the tracks, 
# looking at all the information available from all the different df we have at our disposal

#import math
class Track():
    # the instances of this class are songs, identified using either a combination of their
    # title and artist names, or an identifier when available
    # we track in which file we found the track for (appearance), as well as rating, genre and whether
    # it is in the library or not
    
    def __init__(self, identifier):
        self.identifier = identifier
        self.titles = []
        self.artist = None
        self.is_in_lib = False
        self.appearances = []
        self.genre = []
        self.apple_music_id = []
        self.rating = []
    
    def has_title_name(self, title):
        if title in self.titles:
            return True
        return False
    
    def add_title(self, title):
        self.titles.append(title)
    
    def set_artist(self, artist):
        self.artist = artist
    
    def set_apple_music_id(self, apple_music_id):
        if apple_music_id not in self.apple_music_id:
            self.apple_music_id.append(apple_music_id)
               
    def set_library_flag(self):
        self.is_in_lib = True
    
    def set_genre(self, genre):
        if type(genre) != float:
            if genre not in self.genre:
                self.genre.append(genre.strip())
        
    def add_appearance(self, appearance_dict):
        self.appearances.append(appearance_dict)

    def set_rating(self, rating):
        if rating == 'LOVE' or rating == 'LIKE':
            if rating not in self.rating:
                self.rating.append(rating)
        elif rating == 'DISLIKE':
            if rating not in self.rating:
                self.rating.append(rating)
        
        
#Helper functions     
def concat_title_artist(title, artist):
    '''
        Returns a concatenated string without trailing spaces of the title and
        artist names passed as args
    '''
    return title.strip()+' && '+artist.strip()

def instantiate_track(title, artist):
    '''
        Creates an instance of the Track class, setting both the title and artist
        names used when creating it (multiple titles may be found latter on and added 
        to the list of titles for this track
    '''
    track_instance = Track(increment)
    track_instance.add_title(title)
    track_instance.set_artist(artist)
    return track_instance
            
def update_track_from_library(track_instance, index, row):
    '''
        For a given track instance, updates the properties of the track using the library
        tracks dataframe:
            - its appearance in the library_tracks_info_df, and at which index
            - the genre and rating of the song when available
            - the flag is_in_lib
            - any of the available identifiers used to identify the track
    '''
    track_instance.set_library_flag()
    track_instance.add_appearance({'source': 'library_tracks', 'df_index':index})
    track_instance.set_genre(row['Genre'])
    if row['Genre'] not in genres_list:
        genres_list.append(row['Genre'])
    track_instance.set_rating(row['Track Like Rating'])
    if str(row['Apple Music Track Identifier'])!='nan':
        track_instance.set_apple_music_id(str(int(row['Apple Music Track Identifier'])))
        if str(row['Tag Matched Track Identifier']) !='nan' and row['Tag Matched Track Identifier'] != row['Apple Music Track Identifier']:
            track_instance.set_apple_music_id(str(int(row['Tag Matched Track Identifier'])))
    else:
        track_instance.set_apple_music_id(str(int(row['Track Identifier'])))
        if str(row['Purchased Track Identifier']) !='nan':
            track_instance.set_apple_music_id(str(int(row['Purchased Track Identifier'])))

def update_track_from_play_activity(track_instance, index, row):
    '''
        For a given track instance, updates the properties of the track using the play
        activity dataframe:
            - its appearance in the play_activity_df, and at which index
            - the genre of the song when available
            - the flag is_in_lib whenever the song was found from the library
    '''
    track_instance.add_appearance({'source': 'play_activity', 'df_index':index})
    track_instance.set_genre(row['Genre'])
    if row['Genre'] not in genres_list:
        genres_list.append(row['Genre'])
    if row['Track origin'] == 'library' and track_instance.is_in_lib is False:
            track_instance.set_library_flag()
            
def compare_titles_for_artist(artist, title_to_compare):
    '''
        Compares the string similarity of any song associated to an artist and an unknown
        title for this artist. The goal here is to be able to match different spellings of 
        the same song. 
        If the similarity score is above the threshold set, it returns the track instance
        of the matching artist song we already know. 
        Otherwise it returns 'No match'.
    '''
    for artist_track in artist_tracks_titles[artist]:
        title_similarity_for_artist = similar(title_to_compare, artist_track)
        # value observed to bring consistently a match between similar songs
        if title_similarity_for_artist > 0.625:
            #we fetch the track instance associated with the close match
            title_artist = concat_title_artist(artist_track, artist)
            track_instance = track_instance_dict[title_artist]
            return track_instance
    return 'No match'



In [31]:
columns_to_drop = ['Content Type', 'Sort Name',
'Sort Artist', 'Is Part of Compilation', 'Sort Album',
'Album Artist', 'Track Number On Album',
'Track Count On Album', 'Disc Number Of Album', 'Disc Count Of Album',
'Date Added To iCloud Music Library', 'Last Modified Date',
'Purchase Date', 'Is Purchased', 'Audio File Extension',
'Is Checked', 'Audio Matched Track Identifier', 'Grouping', 'Comments', 
'Beats Per Minute', 'Album Rating', 'Remember Playback Position', 
'Album Like Rating', 'Album Rating Method', 'Work Name', 'Rating',
'Movement Name', 'Movement Number', 'Movement Count',
'Display Work Name', 'Copyright', 'Playlist Only Track',
'Sort Album Artist', 'Sort Composer']

library_tracks_info_df = library_tracks_info_df.drop(columns_to_drop, axis=1)

In [32]:
# First, we build our tracks instances using the library tracks dataframe
def process_library_tracks_df(library_df):
    '''
        This function goes through each row of the library tracks dataframe, creating and updating
        track instances as they appear.
        As this is the first dataframe we go through, we want to create new instances whenever
        we are not facing unknown songs (NaN as a title)
        The logic works as follows, knowing that we do this for each row of the dataframe:
            - we look only at rows with a title different than NaN, and we set the artist to
            'No Artist' if the artist is also Nan
            - if the track is not in the dictionary of track instances, it means that we never
            saw the combination title/artist of this row. So two options here:
                - either we know this artist and we can find a similar title in the artist dict, and in
                this case we update the existing track using update_track_from_library
                - or we do not know this artist, or we do not find a close match of title for this artist
                and in this case we create a new track instance using instantiate_track and then
                update_track_from_library
            - else, we update the existing track using update_track_from_library
    '''
    global increment
    for index, row in library_df.iterrows():
        if str(row['Title']) != 'nan':
            title = row['Title']
            if str(row['Artist']) != 'nan':
                artist = row['Artist']
            else:
                artist = 'No Artist'

            title_artist = concat_title_artist(title, artist)

            if title_artist not in track_instance_dict.keys():
                if artist in artist_tracks_titles.keys():
                    titles_comparison_result = compare_titles_for_artist(artist, title)

                    if titles_comparison_result == 'No match':
                        #we instantiate the Track object
                        track_instance = instantiate_track(title, artist)
                        update_track_from_library(track_instance, index, row)
                        #we update the dictionary that keeps track of our instances, and increment
                        track_instance_dict[title_artist] = track_instance
                        increment+=1

                    else:
                        track_instance = titles_comparison_result
                        if not track_instance.has_title_name(title):
                            track_instance.add_title(title)
                        update_track_from_library(track_instance, index, row)
                        #we also track the match in the track_instances and artist dicts
                        track_instance_dict[title_artist] = track_instance
                        artist_tracks_titles[artist].append(title)
                else:
                    #there was no close match, and the song was never seen, so we instantiate a new Track
                    track_instance = instantiate_track(title, artist)
                    update_track_from_library(track_instance, index, row)
                    #we update the dictionary that keeps track of our instances, and increment
                    track_instance_dict[title_artist] = track_instance
                    increment+=1


            else:
                track_instance = track_instance_dict[title_artist]
                update_track_from_library(track_instance, index, row)


            #we update the artist/track names dictionnary
            if artist not in artist_tracks_titles:
                artist_tracks_titles[artist]=[]
            if title not in artist_tracks_titles[artist]:
                artist_tracks_titles[artist].append(title)
        else:
            items_not_matched['library_tracks'].append(index)



In [33]:
# Then we move on to the identifier information dataframe, to try to match each id with another title

def process_identifier_df(identifier_df):
    '''
        This function goes through each row of the identifier information dataframe, updating
        track instances as they appear.
        Unlike for the tracks dataframe, we have very limited information here, just an identifier
        and a title (not even an artist name). So we need to have a different approach, only
        based on the identifiers. Which may excluse some songs... But prevents false positives.
        The logic works as follows, knowing that we do this for each row of the dataframe:
            - we loop through all the track instances we created so far, and see if any of their 
            identifier matches the id of the row we are looking at
            - if it matches, and if we didn't already have the associated title, we add it to the
            list of titles of that track
            - otherwise, we add it to the tracks we could not match and we ignored.
    '''
    global increment
    for index, row in identifier_df.iterrows():
        found_match = False
        for title_name in track_instance_dict.keys():
            track_instance = track_instance_dict[title_name]
            if row['Identifier'] in track_instance.apple_music_id:
                track_instance.add_appearance({'source': 'identifier_info', 'df_index':index})
                if not track_instance.has_title_name(row['Title']):
                    track_instance.add_title(row['Title'])
                found_match = True
                break
        if found_match is False:
            items_not_matched['identifier_info'].append((index, row['Identifier']))


In [34]:
# And finally, we process the play activity df! Let's use df_analysis that has many less columns

def process_play_df(play_activity_df):
    '''
        This function goes through each row of the play activity dataframe, creating and updating
        track instances as they appear.
        As this is the dataframe we are able to get the most information from, we want to create
        new instances whenever we are not facing unknown songs (NaN as a title).The approach is
        very similar to the one used for the library tracks.
        
        The logic works as follows, knowing that we do this for each row of the dataframe:
            - if the track is in the dictionary of track instances, we update the existing
            track using update_track_from_play_activity
            - else, we have two options :
                - either we know this artist and we can find a similar title in the artist dict,
                and in this case we update the existing track using update_track_from_play_activity
                - or we do not know this artist, or we do not find a close match of title for this
                artist and in this case we create a new track instance using instantiate_track and
                then update_track_from_play_activity
    '''
    global increment
    for index, row in play_activity_df.iterrows():
        #we want to look only at rows where the name of the song is available
        if str(row['Title']) != 'nan':
            title = row['Title']
            if str(row['Artist']) != 'nan':
                artist = row['Artist']
            else:
                artist = 'No Artist'
        else:
            items_not_matched['play_activity'].append(index)
            continue

        #we check if we already saw this track (using title and artist names)
        title_artist = concat_title_artist(title, artist)
        if title_artist in track_instance_dict.keys():
            track_instance = track_instance_dict[title_artist]
            update_track_from_play_activity(track_instance, index, row)

        else:
            # if we had no match with title and artist, we look for similarity in the title for the artist
            if artist in artist_tracks_titles.keys():
                titles_comparison_result = compare_titles_for_artist(artist, title)
                if titles_comparison_result == 'No match':
                    #we instantiate the Track object
                    track_instance = instantiate_track(title, artist)
                    update_track_from_play_activity(track_instance, index, row)
                    #we update the dictionary that keeps track of our instances, and increment
                    track_instance_dict[title_artist] = track_instance
                    increment+=1

                else:
                    track_instance = titles_comparison_result
                    if not track_instance.has_title_name(title):
                        track_instance.add_title(title)
                    track_instance.add_appearance({'source': 'play_activity', 'df_index':index})
                    #we also track the match in the track_instances and artist dicts
                    track_instance_dict[title_artist] = track_instance
                    artist_tracks_titles[artist].append(title)

            # else we know we never saw this track because the artist is unknown      
            else:
                #we update the artist/track names dictionnary
                artist_tracks_titles[artist]=[]
                artist_tracks_titles[artist].append(title)

                #we instantiate the Track object
                track_instance = instantiate_track(title, artist)
                update_track_from_play_activity(track_instance, index, row)

                #we update the dictionary that keeps track of our instances, and increment
                track_instance_dict[title_artist] = track_instance
                increment+=1


In [35]:
# now we process the likes_dislikes_df, trying to match the item reference, or the title/artist 

def process_likes_dislikes_df(likes_dislikes_df):
    '''
        This function goes through each row of the likes_dislikes dataframe, updating
        track instances as they appear.
        This dataframe contains a small proportion of all the tracks ever listened to, and/or in
        the library. As a result, we only want to update existing tracks, and not create new ones.
        The logic works as follows, knowing that we do this for each row of the dataframe:
            - we loop through all the track instances we created so far, and see if any of their 
            identifier matches the id of the row we are looking at
            - if we find a match, we update the track with the rating, appearance, and if we didn't
            already have the associated title, we add it to the list of titles of that track
            - else:
                - if the track is in the dictionary of track instances, we update the existing
            track's rating and appearance
                - otherwise, we have two options:
                    - either we know the artist and we can find a similar title in the artist dict,
                and in this case we update the existing track
                    - or we do not know this artist, or we do not find a close match of title for this
                artist and in this case we add it to the tracks we could not match and we ignored
    '''
    global increment 
    for index, row in likes_dislikes_df.iterrows():
        #we want to look only at rows where the name of the song is available
        if str(row['Title']) != 'nan':
            title = row['Title']
            if str(row['Artist']) != 'nan':
                artist = row['Artist']
            else:
                artist = 'No Artist'
        else:
            items_not_matched['likes_dislikes'].append(index)
            continue

        title_artist = concat_title_artist(title, artist)

        # first we check using the Item Reference as an id
        found_match = False
        for title_name in track_instance_dict.keys():
            track_instance = track_instance_dict[title_name]
            if row['Item Reference'] in track_instance.apple_music_id:
                track_instance.add_appearance({'source': 'likes_dislikes', 'df_index':index})
                track_instance.set_rating(row['Preference'])
                if not track_instance.has_title_name(row['Title']):
                    track_instance.add_title(row['Title'])
                    track_instance_dict[title_artist] = track_instance
                    if row['Title'] not in artist_tracks_titles[artist]:
                        artist_tracks_titles[artist].append(title)
                found_match = True
                break

        if found_match is False:
            #we check if we already saw this track (using title and artist names)
            if title_artist in track_instance_dict.keys():
                track_instance = track_instance_dict[title_artist]
                track_instance.add_appearance({'source': 'likes_dislikes', 'df_index':index})
                track_instance.set_rating(row['Preference'])

            else:
                # if we had no match with title and artist, we look for similarity in the title for the artist
                if artist in artist_tracks_titles.keys():
                    titles_comparison_result = compare_titles_for_artist(artist, title)
                    if titles_comparison_result == 'No match':
                        #we add the item to the items_not_matched
                        items_not_matched['likes_dislikes'].append(index)
                        continue
                    else:
                        track_instance = titles_comparison_result
                        if not track_instance.has_title_name(title):
                            track_instance.add_title(title)
                        track_instance.add_appearance({'source': 'likes_dislikes', 'df_index':index})
                        track_instance.set_rating(row['Preference'])
                        track_instance_dict[title_artist] = track_instance
                        artist_tracks_titles[artist].append(title)
                else:
                    #we add the item to the items_not_matched,
                    #we choose not to add it to the Track instances as the amount of information is little
                    #and our reference really is the play activity!
                    items_not_matched['likes_dislikes'].append(index)
                    continue



In [36]:
## this is used to assign a unique id to each track instance
increment = 0

## this is used to keep track of the title/artist combination with the ref of the associated track instance
track_instance_dict = {}

## this is used to keep track of all the titles of an artist, including different spellings of the same title
artist_tracks_titles = {}

## this is used to keep track of all the unique values of genres
genres_list = []

## this is used to keep track of the rows that were not matched in all dataframes processed
## can be used to spot why a given row was excluded from the track instances
items_not_matched = {'library_tracks':[], 'identifier_info':[],
                     'play_activity':[], 'likes_dislikes':[]}


# we process the library tracks
process_library_tracks_df(library_tracks_info_df)

# we process the identifier infos
process_identifier_df(identifier_infos_df)

# we process the play activity
process_play_df(df_analysis)

In [37]:
len(track_instance_dict)

7978

One comment about the number of tracks we have now in the track_instance_dict: we notice that the total number is reasonably higher than the number of unique song titles available in the play activity dataframe. Why is that? Because of the difference in the way the title is reported in the library, and in the play activity df. In this case, chances are the keys of the track_instance_dict point to the same Track instance. However, in some cases we might also observe keys of a "similar" song version that points to another track, and this can be because some songs are in the library but were never listened to. 

So two cases here:
- we managed to match differents titles to the same instance of a Track
- we were unable using the title name, artist name, and even reference id, to match the track to an existing instance, and we created a new one (for a very similar song)

It is starting to look good! Now one last thing we could do is actually add the info available in the likes_dislikes_df (the 'Preference', or rating). This will allow us to obtain a rating for more songs than solely the library songs as we do now.


Let's start by splitting the 'Item Description' column to get a title and an artist. Although we will perform the match on the Item reference, in can be useful to also gather another spelling of the title when it occurs!

In [38]:
# We construct a column title and a column name from the existing Item Description column

likes_dislikes_df['Title'] = likes_dislikes_df['Item Description'].str.split(' -').str.get(1).str.strip()
likes_dislikes_df['Artist'] = likes_dislikes_df['Item Description'].str.split(' - ').str.get(0).str.strip()
likes_dislikes_df

Item Description Preference  \
0    Starshine Orchestra & Singers - California Dre...       LOVE   
1                                  Bénabar - Le Destin       LOVE   
2    Ronit Shapira, Giora Feidman, John Williams & ...       LOVE   
3                               Rag'n'Bone Man - Human       LOVE   
4    Seth Ford-Young - Chopin Nocturne in Bb Minor:...       LOVE   
..                                                 ...        ...   
439                                        MIKA - Rain       LOVE   
440  Sonya Belousova & Giona Ostinelli - Everytime ...       LOVE   
441  Wesley Sprayue - The Force Theme (From "Star W...       LOVE   
442           Stephan F - Astronomia 2K19 (Radio Edit)       LOVE   
443         Felix Jaehn - SICKO (feat. GASHI & FAANGS)    DISLIKE   

                      Created Last Modified Item Reference  \
0    2016-11-18T15:15:30.271Z           NaN      370173289   
1    2018-04-13T09:01:27.348Z           NaN     1349224826   
2    2018-01-04T16:06:50.347Z           NaN       15507573   
3    2017-02-13T12:40:17.457Z           NaN     1173600551   
4    2017-09-24T11:23:00.272Z           NaN     1166694233   
..                        ...           ...            ...   
439  2020-04-20T11:00:06.102Z           NaN     1445314463   
440  2020-04-23T10:27:24.961Z           NaN     1495203993   
441  2020-04-23T10:27:24.961Z           NaN     1358942361   
442  2020-04-25T08:54:57.272Z           NaN     1461750175   
443  2020-04-25T08:57:59.289Z           NaN     1500827444   

                                                 Title  \
0                                  California Dreamin'   
1                                            Le Destin   
2                      Oyf'n Pripetshok / Nacht Aktion   
3                                                Human   
4             Chopin Nocturne in Bb Minor: Op 9, No. 1   
..                                                 ...   
439                                               Rain   
440                                Everytime You Leave   
441  The Force Theme (From "Star Wars") [Piano Edit...   
442                       Astronomia 2K19 (Radio Edit)   
443                       SICKO (feat. GASHI & FAANGS)   

                                                Artist  
0                        Starshine Orchestra & Singers  
1                                              Bénabar  
2    Ronit Shapira, Giora Feidman, John Williams & ...  
3                                       Rag'n'Bone Man  
4                                      Seth Ford-Young  
..                                                 ...  
439                                               MIKA  
440                  Sonya Belousova & Giona Ostinelli  
441                                     Wesley Sprayue  
442                                          Stephan F  
443                                        Felix Jaehn  

[444 rows x 7 columns]

In [39]:
# we process the likes dislikes
process_likes_dislikes_df(likes_dislikes_df)

In [40]:
len(track_instance_dict)

7983

### Cleaning the duplicates from the track data structure

Alright, looking pretty good so far!


Now, let's take a closer look at the Genre and Rating array of each track. We collected this information using multiple dataframes, so let's see if we have similar values or if there are discrepancies with the data coming from different dataframes...

In [41]:
# checking for discrepancies or duplicates in rating
c=0
for title_artist in track_instance_dict.keys():
    instance = track_instance_dict[title_artist]
    if len(instance.rating) > 1:
        print(title_artist, instance.rating)
    elif len(instance.rating) > 0:
        c+=1
print(c)

438


For the ratings, everything seems coherent (we included in the logic of the class to get rid of duplicates)! We managed to collect 414 ratings, out of the 7985 tracks we have and the 444 records in likes_dislikes_df, not too bad!

Now let's take a look at the genres.

In [42]:
# checking for discrepancies or duplicates in genres
c=0
for title_artist in track_instance_dict.keys():
    instance = track_instance_dict[title_artist]
    if len(instance.genre) > 1:
        c+=1
        print(title_artist, instance.genre)


Bad Motherfucker && Biting Elbows ['Alternative Rock', 'Alternative']
Gerstein's Theme && Armand Amar ['Bande originale', 'Soundtrack']
À Quai && Yann Tiersen ['Bande originale', 'Rock']
T'en va pas (Les enfants du Top 50) && Joyce Jonathan ['Pop', 'French Pop']
Quand elle m'aimait && Myriam Morea ["Children's Music", 'Soundtrack']
To Be By Your Side && Nick Cave ['Pop', 'Soundtrack']
Destin && Céline Dion ['Pop', 'French Pop']
Pour que tu m'aimes encore && Céline Dion ['Pop', 'French Pop']
Farewell && Apocalyptica ['Rock', 'Hard Rock']
Nothing Else Matters && Metallica ['Rock', 'Heavy Metal']
Enter Sandman && Metallica ['Metal', 'Heavy Metal']
The Unforgiven && Metallica ['Metal', 'Heavy Metal']
Hymn for the Weekend (Seeb Remix) && Coldplay ['Dance', 'Alternative']
Love Me Like You Do && Ellie Goulding ['Soundtrack', 'Pop']
Bridal Ballad && Hayley Westenra ['Classical', 'Soundtrack']
California Dreamin' && Starshine Orchestra & Singers ['Soundtrack', 'Pop']
Allez ! && Bénabar ['Chanso

In [43]:
print('Number of songs with more than one genre: ', c)

Number of songs with more than one genre:  277


Here it seems very obvious that depending on the source of the information, with the high probability that we associated several different song tracks (id-wise) from Apple Music, the genre reported for a given song can vary. This is actually a great thing for us, as it could allow building up recommendations using more than one genre to match songs!

### Enrichment of the df_analysis using the tracks data structure

So now, we are going to enrich the df_analysis dataframe, that will eventually be our main dataframe for visualization, using some of the information we gathered in our Track data structure.

One first this we should do, is actually add a column with the reference of the track instance for each row. We will do it solely for df_analysis for now, but it could technically also be done for the other df (why not...). 
Note that after this, we will have the reference of the track instance in our dataframe, as well as the reference of all the rows this track appears in our dataframe (appearance object of the track instance).

In [44]:
# add a reference to the track instance object when available
# add column with rating
# add a column with the list of genres

def build_index_track_instance_dict(target_df_label):
    '''
        Returns a dictionary matching the index of the target dataframe with a reference to its
        associated Track instance.
        
        Argument can be of four types, for the four df we used to build the Track instances:
            - play_activity
            - library_tracks
            - likes_dislikes
            - identifier_infos
    '''
    
    match_index_instance={}
    for title_artist in track_instance_dict.keys():
        instance = track_instance_dict[title_artist]
        for appearance in instance.appearances:
            if target_df_label in appearance['source']:
                if appearance['df_index'] not in match_index_instance:
                    match_index_instance[appearance['df_index']] = []
                if instance not in match_index_instance[appearance['df_index']]:
                    match_index_instance[appearance['df_index']].append(instance)
                    match_index_instance[appearance['df_index']].append(instance.is_in_lib)
                    match_index_instance[appearance['df_index']].append(instance.rating)
                    match_index_instance[appearance['df_index']].append(instance.genre)
                    

    return match_index_instance

# we build the dictionary matching df_analysis indexes with track instance ref
match_index_instance_activity = build_index_track_instance_dict('play_activity')  

# we convert this dictionary into a df, that we merge with df_analysis to have a new column 
# containing the ref to the instance
index_instance_df = pd.DataFrame.from_dict(match_index_instance_activity, orient='index', columns=['Track Instance', 'Library Track', 'Rating', 'Genres'])
df_visualization = df_analysis.drop(['Genre'], axis=1)
df_visualization = pd.concat([df_visualization,index_instance_df], axis=1)


In [45]:
df_visualization

Artist                                           Title  \
0                    NaN                                             NaN   
1                    NaN                                             NaN   
2                    NaN                                             NaN   
3                    NaN                                             NaN   
4      How to Dress Well  World I Need You, Won't Be Without You (Proem)   
...                  ...                                             ...   
25397       Klaus Badelt                                   One Last Shot   
25398        Cosmic Baby                               Movements In Love   
25399   Lindsey Stirling                    Shatter Me (feat. Lzzy Hale)   
25400  Antti Martikainen                                       Legendary   
25401            Ricoune                         On a le web à la maison   

                    Content Provider           End Reason Type Event Type  \
0                                NaN            NOT_APPLICABLE   PLAY_END   
1                                NaN            NOT_APPLICABLE   PLAY_END   
2                                NaN            NOT_APPLICABLE   PLAY_END   
3                                NaN            NOT_APPLICABLE   PLAY_END   
4          Domino Recording Co. Ltd.      NATURAL_END_OF_TRACK   PLAY_END   
...                              ...                       ...        ...   
25397                     UMG Global  PLAYBACK_MANUALLY_PAUSED   PLAY_END   
25398          Kontor New Media GmbH      NATURAL_END_OF_TRACK   PLAY_END   
25399  Universal Music International  PLAYBACK_MANUALLY_PAUSED   PLAY_END   
25400           PK Interactive, Inc.      NATURAL_END_OF_TRACK   PLAY_END   
25401                  TuneCore, Inc      NATURAL_END_OF_TRACK   PLAY_END   

                             Item Type  Offline  \
0      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
1      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
2      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
3      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
4                 ITUNES_STORE_CONTENT    False   
...                                ...      ...   
25397             ITUNES_STORE_CONTENT    False   
25398             ITUNES_STORE_CONTENT    False   
25399             ITUNES_STORE_CONTENT    False   
25400             ITUNES_STORE_CONTENT    False   
25401             ITUNES_STORE_CONTENT    False   

                    Activity date time  Play Year  Play Month  ...   Play DOW  \
0     2018-04-09 14:11:10.613000+00:00       2018           4  ...     Monday   
1     2018-04-09 12:39:02.454000+00:00       2018           4  ...     Monday   
2     2018-01-02 14:39:29.744000+00:00       2018           1  ...    Tuesday   
3     2016-12-02 07:22:34.766000+00:00       2016          12  ...     Friday   
4     2018-01-07 10:34:13.327000+00:00       2018           1  ...     Sunday   
...                                ...        ...         ...  ...        ...   
25397 2016-08-16 08:01:27.899000+00:00       2016           8  ...    Tuesday   
25398 2017-11-02 14:09:34.498000+00:00       2017          11  ...   Thursday   
25399 2018-09-25 09:16:41.844000+00:00       2018           9  ...    Tuesday   
25400 2018-11-21 15:44:40.824000+00:00       2018          11  ...  Wednesday   
25401 2018-01-22 09:46:34.284000+00:00       2018           1  ...     Monday   

      Play HOD UTC  Play HOD Local Time  Played completely     Track origin  \
0               14                   14               True            other   
1               12                   12               True            other   
2               14                   14               True            other   
3                7                    7               True            other   
4               10                   11               True           search   
...            ...                  ...                ...              ...   
25397            8                   10  

Now let's clean it up so we can actually use it straight away to plot visualizations!

In [46]:
def clean_col_with_list(x):
    '''
        This function is used to break down the values of a serie containing lists.
        The idea is to return the values as a string ('', the unique value of a list, or a join of
        values separated by '&&').
    '''
    if type(x) != float:
        if x == None or len(x) == 0:
            return 'Unknown'
        elif len(x) == 1:
            return x[0]
        else:
            return ' && '.join(x)
    else:
        return 'Unknown'
    
df_visualization['Rating'] = df_visualization['Rating'].apply(clean_col_with_list)
df_visualization['Genres'] = df_visualization['Genres'].apply(clean_col_with_list)

In [47]:
# Let's also replace nan value from genres_list and make sure we do not have extra spaces

genres_list_clean = [x if str(x) != 'nan' else '' for x in genres_list]
genres_list_clean = [x.strip() for x in genres_list_clean]

In [48]:
df_visualization

Artist                                           Title  \
0                    NaN                                             NaN   
1                    NaN                                             NaN   
2                    NaN                                             NaN   
3                    NaN                                             NaN   
4      How to Dress Well  World I Need You, Won't Be Without You (Proem)   
...                  ...                                             ...   
25397       Klaus Badelt                                   One Last Shot   
25398        Cosmic Baby                               Movements In Love   
25399   Lindsey Stirling                    Shatter Me (feat. Lzzy Hale)   
25400  Antti Martikainen                                       Legendary   
25401            Ricoune                         On a le web à la maison   

                    Content Provider           End Reason Type Event Type  \
0                                NaN            NOT_APPLICABLE   PLAY_END   
1                                NaN            NOT_APPLICABLE   PLAY_END   
2                                NaN            NOT_APPLICABLE   PLAY_END   
3                                NaN            NOT_APPLICABLE   PLAY_END   
4          Domino Recording Co. Ltd.      NATURAL_END_OF_TRACK   PLAY_END   
...                              ...                       ...        ...   
25397                     UMG Global  PLAYBACK_MANUALLY_PAUSED   PLAY_END   
25398          Kontor New Media GmbH      NATURAL_END_OF_TRACK   PLAY_END   
25399  Universal Music International  PLAYBACK_MANUALLY_PAUSED   PLAY_END   
25400           PK Interactive, Inc.      NATURAL_END_OF_TRACK   PLAY_END   
25401                  TuneCore, Inc      NATURAL_END_OF_TRACK   PLAY_END   

                             Item Type  Offline  \
0      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
1      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
2      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
3      AGGREGATE_NON_CATALOG_PLAY_TIME    False   
4                 ITUNES_STORE_CONTENT    False   
...                                ...      ...   
25397             ITUNES_STORE_CONTENT    False   
25398             ITUNES_STORE_CONTENT    False   
25399             ITUNES_STORE_CONTENT    False   
25400             ITUNES_STORE_CONTENT    False   
25401             ITUNES_STORE_CONTENT    False   

                    Activity date time  Play Year  Play Month  ...   Play DOW  \
0     2018-04-09 14:11:10.613000+00:00       2018           4  ...     Monday   
1     2018-04-09 12:39:02.454000+00:00       2018           4  ...     Monday   
2     2018-01-02 14:39:29.744000+00:00       2018           1  ...    Tuesday   
3     2016-12-02 07:22:34.766000+00:00       2016          12  ...     Friday   
4     2018-01-07 10:34:13.327000+00:00       2018           1  ...     Sunday   
...                                ...        ...         ...  ...        ...   
25397 2016-08-16 08:01:27.899000+00:00       2016           8  ...    Tuesday   
25398 2017-11-02 14:09:34.498000+00:00       2017          11  ...   Thursday   
25399 2018-09-25 09:16:41.844000+00:00       2018           9  ...    Tuesday   
25400 2018-11-21 15:44:40.824000+00:00       2018          11  ...  Wednesday   
25401 2018-01-22 09:46:34.284000+00:00       2018           1  ...     Monday   

      Play HOD UTC  Play HOD Local Time  Played completely     Track origin  \
0               14                   14               True            other   
1               12                   12               True            other   
2               14                   14               True            other   
3                7                    7               True            other   
4               10                   11               True           search   
...            ...                  ...                ...              ...   
25397            8                   10  

### Conclusion of the feature construction

OK.... So let's summarize what we have so far....

We built a visualization df that contains:
- play activity information, such as when the track was listened to with a breakdown in time (year, month, day of month, day of week, hour of the day), if it was skipped, ....
- a reference to the track instance (can be used to fetch additional information, such as all the titles used to describe it)
- whether the song (or a similar track based on its title) is in the library
- the genre(s) associated to each song when available
- the rating (liked/disliked)
- how the song was found (suggestion, search, library,....)

So from there on, let's enumerate the angles of analysis that we want to follow!

1. Are there any trends on the moment songs are listened to? Does it change from one year to another? What's the average listening time per day/week/month across years?
2. What are the genres most LIKED, most DISLIKED? Is there a link between the origin of the track and its rating?
3. Where are songs most usually found? How are found songs in the library (evaluation of the relevance of the suggestions)? 
4. What's the ratio of songs skipped? Is there a link between the origin of the track, its rating, and whether it was skipped or not? 
5. Can we establish a ranking of artists? Of genres? Is there a difference between the years we observe?
6. General appreciation of how much time songs are listened to, using some filters per year, artist, genre....
7. Life cycle of a song (listened to for a long period, vs short period)

Optional questions:
- Comparison of songs listened to vs when they were released
- Variation calculation with previous year/month/week stats

Based on these axis of analysis, let's see if there are any features and rows that don't make sense to be kept for the analysis later on.


In [49]:
df_visualization.isnull().sum()

Artist                      876
Title                       876
Content Provider            876
End Reason Type             458
Event Type                    0
Item Type                     0
Offline                       0
Activity date time            0
Play Year                     0
Play Month                    0
Play DOM                      0
Play DOW                      0
Play HOD UTC                  0
Play HOD Local Time           0
Played completely             0
Track origin                  0
Play duration in minutes      0
Track Instance              876
Library Track               876
Rating                        0
Genres                        0
dtype: int64

So we can observe two trends in the number of missing values:
- some columns have 458 missing values
- some columns have 876 missing values

When it comes to 485 missing values, it is because we do not even have informations about when the song was listened to, but it can happen that we have details about the songs themselves. We notice, indeed, that in these case the majority of the tracks were skipped - so not listened to. 

When it comes to 876, it is related to the songs with an unknown title. As a result, we have only information about when the song was listened to, but we don't actually which song it is. As we still know when the song was listened to, to plot time of activity trends, those rows are useful. So let's keep them.

Now one tiny little last thing to do: let's remove the space in the name of the columns for convenience later on when we want to query rows usign the column names as an attribute of the dataframe.

In [50]:
df_visualization.columns = [c.replace(' ', '_') for c in df_visualization.columns]

In [51]:
df_visualization.columns

Index(['Artist', 'Title', 'Content_Provider', 'End_Reason_Type', 'Event_Type',
       'Item_Type', 'Offline', 'Activity_date_time', 'Play_Year', 'Play_Month',
       'Play_DOM', 'Play_DOW', 'Play_HOD_UTC', 'Play_HOD_Local_Time',
       'Played_completely', 'Track_origin', 'Play_duration_in_minutes',
       'Track_Instance', 'Library_Track', 'Rating', 'Genres'],
      dtype='object')

## Data visualization

Alrigt, so now let's start exploring the data with plots, to find out some trends !


### Listening moments trends

We are trying to answer the following questions:
- Are there any trends on the moment songs are listened to? 
- Does it change from one year to another? 

In [52]:
#plotting the repartition of listening times per year

labels = df_visualization['Play_Year'].unique()[:-1]
values = df_visualization['Play_Year'].value_counts()

fig = go.Figure(data=[go.Pie(labels=labels, 
                             values=values,
                             textinfo='label+percent',
                             hoverinfo='none')])
fig.update_layout(
    title='Distribution in percentage of the year tracks were listened to',
    showlegend=False
)


fig.show()

In [53]:
# plot the distribution of tracks listened to per month for different years

fig = go.Figure(data=[
    go.Bar(name='2016',
           x=df_visualization[df_visualization['Play_Year']==2016]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2016]['Play_Month'].value_counts(),
           marker_color='rgb(253, 231, 37)'
    ),
    go.Bar(name='2017',
           x=df_visualization[df_visualization['Play_Year']==2017]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2017]['Play_Month'].value_counts(),
           marker_color='rgb(68, 1, 84)'
    ),
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'].value_counts(),
           marker_color='rgb(49, 104, 142)'
    ),
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2019]['Play_Month'].value_counts(),
           marker_color='rgb(31, 158, 137)'
    ),
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2020]['Play_Month'].value_counts(),
           marker_color='rgb(180, 222, 44)'
    )
])

#update the layout
fig.update_layout(
    title='Distribution of the number of tracks listened to each month for different years',
    xaxis=dict(
        #title='Month of the year',
        tickangle = -45,
        tickmode = 'array',
        tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
        ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
    ),
    yaxis=dict(
        title='Number of tracks listened to',
        titlefont_size=16,
        tickfont_size=14,
    ),
    barmode='group',
)


fig.show()

In [54]:
# plot the distribution of tracks listened to per day of the month for different years

fig = make_subplots(rows=5, cols=1, y_title='Number of tracks listened to',)

fig.add_trace(
    go.Bar(name='2016',
           x=df_visualization[df_visualization['Play_Year']==2016]['Play_DOM'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2016]['Play_DOM'].value_counts(),
           marker_color='rgb(253, 231, 37)'
    ),
    row=1, col=1
)

fig.add_trace(
    go.Bar(name='2017',
           x=df_visualization[df_visualization['Play_Year']==2017]['Play_DOM'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2017]['Play_DOM'].value_counts(),
           marker_color='rgb(68, 1, 84)'
    ),
    row=2, col=1
)

fig.add_trace(
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_DOM'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2018]['Play_DOM'].value_counts(),
           marker_color='rgb(49, 104, 142)'
    ),
    row=3, col=1
)

fig.add_trace(
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_DOM'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2019]['Play_DOM'].value_counts(),
           marker_color='rgb(31, 158, 137)'
    ),
    row=4, col=1
)

fig.add_trace(
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_DOM'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2020]['Play_DOM'].value_counts(),
           marker_color='rgb(180, 222, 44)'
    ),
    row=5, col=1
)

fig.update_layout(
    title='Distribution of the number of tracks listened to each day of the month for different years',
    height=800
)

fig.show()




In [55]:
# plot the distribution of tracks listened to per day of the week for different years

def compute_ratio_songs(serie):
    return (serie.value_counts()/serie.count())*100

fig = go.Figure(data=[
    go.Bar(name='2016',
           x=df_visualization[df_visualization['Play_Year']==2016]['Play_DOW'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2016]['Play_DOW']),
           marker_color='rgb(253, 231, 37)'
    ),
    go.Bar(name='2017',
           x=df_visualization[df_visualization['Play_Year']==2017]['Play_DOW'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2017]['Play_DOW']),
           marker_color='rgb(68, 1, 84)'
    ),
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_DOW'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2018]['Play_DOW']),
           marker_color='rgb(49, 104, 142)'
    ),
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_DOW'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2019]['Play_DOW']),
           marker_color='rgb(31, 158, 137)'
    ),
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_DOW'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2020]['Play_DOW']),
           marker_color='rgb(180, 222, 44)'
    )
])

#update the layout
fig.update_layout(
    title='Distribution of percentage of tracks listened to per day of the week for different years',
    xaxis=dict(
        categoryorder='array',
        tickangle = -45,
        categoryarray = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday'],
    ),
    yaxis=dict(
        title='Percentage of tracks listened to per year',
        titlefont_size=16,
        tickfont_size=14,
    ),
    barmode='group',
)


fig.show()

In [132]:
# plot the distribution of tracks listened to per hour of the day for different years

fig = make_subplots(rows=5, cols=1, y_title='Percentage of tracks listened to')

fig.add_trace(
    go.Bar(name='2016',
           x=df_visualization[df_visualization['Play_Year']==2016]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2016]['Play_HOD_Local_Time']),
           marker_color='rgb(253, 231, 37)'
    ),
    row=1, col=1
)

fig.add_trace(
    go.Bar(name='2017',
           x=df_visualization[df_visualization['Play_Year']==2017]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2017]['Play_HOD_Local_Time']),
           marker_color='rgb(68, 1, 84)'
    ),
    row=2, col=1
)

fig.add_trace(
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2018]['Play_HOD_Local_Time']),
           marker_color='rgb(49, 104, 142)'
    ),
    row=3, col=1
)

fig.add_trace(
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2019]['Play_HOD_Local_Time']),
           marker_color='rgb(31, 150, 139)'
    ),
    row=4, col=1
)

fig.add_trace(
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2020]['Play_HOD_Local_Time']),
           marker_color='rgb(184, 222, 41)'
    ),
    row=5, col=1
)

fig.update_layout(
    title='Distribution of percentage of tracks listened to per hour of the day for different years (in local time)',
    height=800
)
fig.update_xaxes(matches='x')

fig.show()

**Conclusion**

So can we see trends? Clearly!
1. 2018 is by far the most active year. Although 2016 was only partial, it is almost as active as the whole year 2019. 
2. We need to be careful with the analysis per month, as both 2016 and 2020 are partial years. Looking at 2017, 2018 and 2019, there are two main trends common : May, November and December are the least active months, and the beginning of the year tends in general to be more active that the middle and end of the year. 
3. When it comes to the day of the week, trends are different between the few years. But in general, activity is slower in the weekend than during the week. Exception of 2019, when my schedule actually changed and every day became work day
4. When we look at the distrution per day of the month, we can actually spot waves periodically, there is no moment of the month I tend to listen to more music. It is more relevant to look at the weekly breakdown.
5. Tracks are listened to during the day between let's say 8am and 7pm, with two main picks, one in the morning and one in the afternoon. These trends are observed for all years, with a closer similarity for 2017, 2018 and 2019 (again, 2016 and 2020 are incomplete years, and I changes my schedule of work in 2020!).


### Listening duration

So here we are trying to get a general appreciation of how much time songs are listened to each day, filtered per artist, genre, origin, title,.... This will also provide an insight on the average playing time, and the life cycle of a song/artist/genre (if it is listened to a lot for some time, then not,....).

Let's try to build a more complicated visualization, a heatmap, that will show for each single day of our dataset the number of minutes played. 

Later on we will play with filters on this visualization.

In [57]:
fig = go.Figure(go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2018]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=-1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2018]['Play_duration_in_minutes'],
        histfunc="sum"
    ))

fig.update_layout(
    title='Heat map of the play duration in minutes for each day - 2018',
    xaxis=dict(
        tickangle = -45,
        tickmode = 'array',
        tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
        ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
    ),
)


fig.show()

Alright so now that we manage to plot this heat map of the listening time per day of each month for one year, let's plot it for all years so we can actually compare the trends across years.

In [58]:
fig = make_subplots(rows=5, cols=1, y_title='Day of the month',
                    subplot_titles=("2016", "2017", "2018", "2019", "2020"))

fig.add_trace(
    go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2016]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2016]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2016]['Play_duration_in_minutes'],
        histfunc="sum",
        coloraxis="coloraxis",
        hovertemplate=
        "<b>%{y} %{x} 2016</b><br>" +
        "Time listening: %{z:,.0f} minutes<br>" +
        "<extra></extra>",
    ),
    row=1, col=1
)

fig.add_trace(
    go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2017]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2017]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2017]['Play_duration_in_minutes'],
        histfunc="sum",
        coloraxis="coloraxis",
        hovertemplate=
        "<b>%{y} %{x} 2017</b><br>" +
        "Time listening: %{z:,.0f} minutes<br>" +
        "<extra></extra>",
    ),
    row=2, col=1
)

fig.add_trace(
    go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2018]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2018]['Play_duration_in_minutes'],
        histfunc="sum",
        coloraxis="coloraxis",
        hovertemplate=
        "<b>%{y} %{x} 2018</b><br>" +
        "Time listening: %{z:,.0f} minutes<br>" +
        "<extra></extra>",
    ),
    row=3, col=1
)

fig.add_trace(
    go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2019]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2019]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2019]['Play_duration_in_minutes'],
        histfunc="sum",
        coloraxis="coloraxis",
        hovertemplate=
        "<b>%{y} %{x} 2019</b><br>" +
        "Time listening: %{z:,.0f} minutes<br>" +
        "<extra></extra>",
    ),
    row=4, col=1
)

fig.add_trace(
    go.Histogram2d(
        y=df_visualization[df_visualization['Play_Year']==2020]['Play_DOM'],
        x=df_visualization[df_visualization['Play_Year']==2020]['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=df_visualization[df_visualization['Play_Year']==2020]['Play_duration_in_minutes'],
        histfunc="sum",
        coloraxis="coloraxis",
        hovertemplate=
        "<b>%{y} %{x} 2020</b><br>" +
        "Time listening: %{z:,.0f} minutes<br>" +
        "<extra></extra>",
    ),
    row=5, col=1
)


fig.update_layout(
    title='Heat map of the play duration in minutes for each day',
    height=2000,
    coloraxis=dict(colorscale='hot'),
    showlegend=False,
)

fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=1, col=1)
fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=2, col=1)
fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=3, col=1)
fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=4, col=1)
fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=5, col=1)

fig.update_xaxes(matches='x')

fig.show()

Now let's see if we can find a way to filter on the artist, or the genre, or the origin of the tracks, or whether we like/disliked the song.

In [59]:
def manage_query_filters(query_type, query_values, year):
    '''
        This function returns a query that can be used to filter the dataframe.
        It takes as an input a query_type, of type str, that can take the following values:
            - genre
            - artist
            - title
            - rating
            - origin
            - offline
        It takes as a second argument query_values, a list of strings, that should contain
        any of the strings that we want to match to the query_type. For example, we can search
        for ['Pop', 'Rock', 'Soundtrack'] in query_type == 'genre'. The search uses partial match
        with OR (if the column Genres of the df contains any of these strings).
        
        Finally, it takes as a argument the year we want to filter for (passed as an input
        for the query, and not as an argument for the plot)
    '''
    if query_values == [] or query_type == '':
        query = build_data_query('', [], year)
    else:
        query = build_data_query(query_type, query_values, year)
    return query

def build_query_element(category, query_values):
    '''
        This function builds the string that is used as a query to filter the dataframe.
        Depending on the number of arguments passed in query_values, the format of the query changes.
        Mix of AND between the date and the category search, and OR between each value of the
        category we want to search for.
        
        Example:
        year 2018 AND (genre 'Pop' OR 'Rock' OR 'Soundtrack')
    '''
    query_element = '&'
    if len(query_values) == 1:
        query_element = query_element + '{0}.str.contains("{1}")'.format(category, query_values[0])
    elif len(query_values) == 2:
        first_item = '{0}.str.contains("{1}")'.format(category, query_values[0])
        last_item = '{0}.str.contains("{1}")'.format(category, query_values[-1])
        query_element = query_element + '(' + first_item + '|' + last_item + ')'
    else:
        first_item = '{0}.str.contains("{1}")'.format(category, query_values[0])
        last_item = '{0}.str.contains("{1}")'.format(category, query_values[-1])
        query_element = query_element + '(' + first_item + '|'
        for k in range(1, len(query_values)-1):
            query_element = query_element + '{0}.str.contains("{1}")'.format(category, query_values[k]) + '|'
        query_element = query_element + last_item + ')'
    
    return query_element


def build_data_query(query_type, query_values, year):
    '''
        This function is in charge of choosing which column to use in the query 
        depending on the query_type selected.
        It uses build_query_element to actually put together the query string.
    '''
    query = 'Play_Year=={0}'.format(year)
    if query_type == 'genre':
        query = query + build_query_element('Genres', query_values)
    elif query_type == 'artist':
        query = query + build_query_element('Artist', query_values)
    elif query_type == 'title':
        query = query + build_query_element('Title', query_values)
    elif query_type == 'rating':
        query = query + build_query_element('Rating', query_values)
    elif query_type == 'origin':
        query = query + build_query_element('Track_origin', query_values)
    elif query_type == 'offline':
        # as here we compare with booleans, we do not use build_query_element
        if len(query_values) == 1:
            query = query + '&{0}.isin([{1}])'.format('Offline', query_values[0])
        else:
            first_item = '{0}.isin([{1}]'.format('Offline', query_values[0])
            last_item = '{0}.isin([{1}])'.format('Offline', query_values[-1])
            query = query + '&(' + first_item + '|' + last_item + ')'
    else:
        #query is only filtered on the year, total amount of time without filters
        query = query
    return query



In [60]:
# Helper function to build a dictionary of the listening time per day/month 
#from the filtered df using the query (query includes the year to filter for)
# Note that this function is not currently used in this notebook

def df_to_plotly(df, query):
    '''
        This function builds a dictionary using (month, day) as a key
        and the total listening time associated to it.
        The dataframe passed as an input should be filtered out using a query also
        passed as an attribute, for example to get a dictionary per year, or for a 
        particular match of genre, artist....
        The output dictionary can then be used to plot the listening time.
    '''
    plotly_dict = {}
    g = df.query(query).groupby(['Play_Month', 'Play_DOM'])
    for key in g.groups.keys():
        total_listening_time = 0
        for value in g.groups[key]:
            listening_time = df.iloc[value]['Play_duration_in_minutes']
            total_listening_time += listening_time
        plotly_dict[key] = total_listening_time
    return plotly_dict

#df_to_plotly(df_visualization, query)

In [61]:
def render_heatmap(df, years, query_type, query_values):
    '''
        This function is in charge of building and rendering the heatmaps 
        corresponding to a particular set of conditions (years, filters on genre,
        artist, ...)
        It relies on the render_trace function to build each trace of the subplots.
    '''
    rows = len(years)
    row = 1
    sub_titles = [str(x) for x in years]
    height = 0
    fig = make_subplots(rows=rows, cols=1, y_title='Day of the month',
                       subplot_titles=sub_titles)
    
    for year in years:
        query = manage_query_filters(query_type, query_values, year)
        filtered_df = df.query(query)
        render_trace(fig, row, filtered_df, years[row-1])
        sub_titles.append(years[row-1])
        row += 1
        height += 500
        
    fig.update_layout(
        title='Heat map of the play duration in minutes for each day',
        height = height,
        coloraxis=dict(colorscale='viridis'),
        showlegend=False,
    )
    
    fig.update_xaxes(matches='x')
    fig.show()
    
def render_trace(fig, row, df, year):
    '''
        This function is in charge of building a single 2D Histogram trace.
    '''
    fig.add_trace(
        go.Histogram2d(
            y=df['Play_DOM'],
            x=df['Play_Month'],
            autobiny=False,
            ybins=dict(start=0.5, end=31.5, size=1),
            autobinx=False,
            xbins=dict(start=0.5, end=12.5, size=1),
            z=df['Play_duration_in_minutes'],
            histfunc="sum",
            coloraxis="coloraxis",
            hovertemplate=
            "<b>%{y} %{x}</b><b> "+str(year)+"<b><br>" +
            "Time listening: %{z:,.0f} minutes<br>" +
            "<extra></extra>",
        ),
        row=row, col=1
    )
    fig.update_xaxes(tickangle = -45, tickmode = 'array', tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
                 ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December'],
                 row=row, col=1)
    


Now let's try to plot the heat maps for a few filters.

In [62]:
query_type = 'genre'
query_values = ['Soundtrack']

render_heatmap(df_visualization, [2016, 2017, 2018, 2019, 2020], query_type, query_values)


In [63]:
query_type = 'artist'
query_values = ['Pink Floyd']

render_heatmap(df_visualization, [2019], query_type, query_values)

In [64]:
query_type = 'origin'
query_values = ['search']

render_heatmap(df_visualization, [2017, 2018], query_type, query_values)

In [65]:
query_type = 'origin'
query_values = ['for you']

render_heatmap(df_visualization, [2016, 2020], query_type, query_values)

Brilliant! We can visualize in great details the trends of our listening activity, filtering using so many properties!

In [66]:
query_type = 'offline'
query_values = [True]

render_heatmap(df_visualization, [2017], query_type, query_values)

### Ranking

We are now ready to move on to the next big topic: ranking!

So here we will try to figure out:
- what are the genres, artists most LIKED/DISLIKED
- what are the top X genres, artists, titles listened to (in terms of count)
- if there is a link between how the track was found and its rating



In [221]:
#Let's define a function to get the count of songs per genre, provided a df

def build_genres_count_dict(df_genres, genres_list):
    genres_count_dict = {}
    for ref_genre in genres_list:
        genres_count_dict[ref_genre] = 0
    for df_genre in df_genres.tolist():
        if '&&' in df_genre:
            genres = df_genre.split('&&')
            for genre in genres:
                if genre.strip() in genres_count_dict.keys():
                    genres_count_dict[genre.strip()] += 1
        else:
            if df_genre in genres_count_dict.keys():
                genres_count_dict[df_genre] += 1
    return genres_count_dict

def build_count_dict(df_target):
    ref_list = df_target.unique()
    
    count_dict = {}
    for ref_elem in ref_list:
        if str(ref_elem) != 'nan':
            count_dict[ref_elem] = 0
    for df_elem in df_target.tolist():
        if str(df_elem) != 'nan':
            if df_elem in count_dict.keys():
                count_dict[df_elem] += 1
        else:
            continue      
    return count_dict

def build_ranking_dict_per_year(df, ranking_target, years, query_type, query_values):
    ranking_dict = {}
    for year in years:
        query = manage_query_filters(query_type, query_values, year)
        filtered_df = df_visualization.query(query)
        if ranking_target == 'Genres':
            ranking_dict[year] = build_genres_count_dict(filtered_df[ranking_target], genres_list_clean)
        elif ranking_target in ['Artist', 'Track_origin', 'Title']:
            ranking_dict[year] = build_count_dict(filtered_df[ranking_target])   
    return ranking_dict


In [238]:
def build_sunburst_arrays(genres_dict, ranking_target):
    labels = []
    parents = []
    values = []
    ids = []
    for year in genres_dict.keys():
        current_index = len(labels)
        ids.append(str(year))
        labels.append(str(year))
        parents.append(ranking_target)
        total_count = 0
        for genre in genres_dict[year].keys():
            ids.append(str(year)+' - '+genre)
            labels.append(genre)
            parents.append(str(year))
            values.append(genres_dict[year][genre])
            total_count += genres_dict[year][genre]
        values.insert(current_index, total_count)
    return labels, parents, values, ids



def render_sunburst_plot(df, ranking_target, years, query_type, query_values):
    ranking_dict = build_ranking_dict_per_year(df, ranking_target, years, query_type, query_values)
    labels, parents, values, ids = build_sunburst_arrays(ranking_dict, ranking_target)
    fig =go.Figure(go.Sunburst(
        ids=ids,
        labels=labels,
        parents=parents,
        values=values,
        branchvalues="total",
        insidetextorientation='radial'
    ))
    # Update layout for tight margin
    fig.update_layout(
        title = 'Ranking across years of ' + ranking_target,
        margin = dict(l=0, r=0, b=0),
    )

    fig.show()
    

years = [2016, 2017, 2018, 2019, 2020]
viridis_colors = ['#440154FF', '#481567FF', '#482677FF', '#453781FF', '#404788FF',
                  '#39568CFF', '#33638DFF', '#2D708EFF', '#287D8EFF', '#238A8DFF',
                  '#1F968BFF', '#20A387FF', '#29AF7FFF', '#3CBB75FF', '#55C667FF',
                  '#73D055FF', '#95D840FF', '#B8DE29FF', '#DCE319FF', '#FDE725FF']



In [239]:
query_type = ''
query_values = []

render_sunburst_plot(df_visualization, 'Genres', [2016, 2017, 2018, 2019, 2020], query_type, query_values)



In [240]:
query_type = 'rating'
query_values = ['LOVE']

render_sunburst_plot(df_visualization, 'Genres', [2017, 2018, 2019], query_type, query_values)



Alright! Looks great!

Note that it is possible to also render this graph using artists and titles, but for obvious reasons, it takes a lot more time to compute and is not as readable due to the higher number of unique values available!

In [235]:
query_type = 'rating'
query_values = ['LOVE']

render_sunburst_plot(df_visualization, 'Artist', [2017, 2018, 2019], query_type, query_values)

So for artists and titles, let's use instead a ranked list, with the associated count value.

In [201]:
def list_top_ranked(df, ranking_target, num_ranks, years, query_type, query_values):
    ranking_dict = build_ranking_dict(df, ranking_target, years, query_type, query_values)
    for year in years:
        ranking = {key: ranking_dict[year][key] for key in sorted(ranking_dict[year], key=ranking_dict[year].get, reverse=True)[:num_ranks]}
        print('Top ranking for '+ str(year))
        print('   ', ranking)
        print('\n')


In [202]:
query_type = 'rating'
query_values = ['LOVE']

list_top_ranked(df_visualization, 'Artist', 5, [2017, 2018, 2019], query_type, query_values)

Top ranking for 2017
    {'Metallica': 104, 'John Ottman': 58, 'Bastille': 53, 'Stromae': 44, 'Hayley Westenra': 44}


Top ranking for 2018
    {'Lindsey Stirling': 269, 'Los Hermanos': 115, 'Antti Martikainen': 98, 'Bénabar': 69, 'Céline Dion': 65}


Top ranking for 2019
    {'Lindsey Stirling': 153, 'Emmanuel Moire': 112, 'Amel Bent': 94, 'Céline Dion': 81, 'Armin van Buuren': 75}




In [205]:
query_type = 'rating'
query_values = ['LOVE']

list_top_ranked(df_visualization, 'Title', 5, [2017, 2018, 2019, 2020], query_type, query_values)

Top ranking for 2017
    {'Master of Puppets': 74, 'Main Theme': 58, 'Things We Lost in the Fire': 53, 'Sunshine': 41, 'Esperanças Perdidas': 36}


Top ranking for 2018
    {'The Crown of War': 87, 'Master of Tides': 69, 'Deixa o Verão': 67, 'Je ne sais rien': 56, 'Le Destin': 49}


Top ranking for 2019
    {'Dis-moi qui tu es': 94, 'Deixa o Verão': 60, 'Layla': 57, 'Carol of the Bells': 52, 'La femme au milieu': 41}


Top ranking for 2020
    {'Kings & Queens': 45, 'Russian Music Box (2000)': 29, 'Loreley': 28, 'Whenever, Wherever': 25, 'Let the Music Guide You (Asot 950 Anthem)': 18}




In [203]:
query_type = ''
query_values = []

list_top_ranked(df_visualization, 'Genres', 10, [2016, 2017, 2018, 2019, 2020], query_type, query_values)

Top ranking for 2016
    {'Soundtrack': 2538, 'Pop': 1133, 'French Pop': 955, 'Classical': 782, 'Rock': 503, 'Alternative': 446, 'Dance': 295, 'Heavy Metal': 228, 'Musicals': 203, 'Hard Rock': 190}


Top ranking for 2017
    {'Soundtrack': 888, 'Pop': 850, 'Classical': 458, 'French Pop': 346, 'Alternative': 312, 'Rock': 284, 'Dance': 182, 'Heavy Metal': 123, 'Singer/Songwriter': 122, 'Electronic': 103}


Top ranking for 2018
    {'Pop': 1305, 'French Pop': 974, 'Soundtrack': 759, 'Rock': 338, 'Alternative': 335, 'Classical': 233, 'Heavy Metal': 208, 'Metal': 177, 'MPB': 125, 'Holiday': 116}


Top ranking for 2019
    {'French Pop': 1266, 'Pop': 1168, 'Soundtrack': 596, 'Dance': 581, 'Rock': 324, 'Alternative': 286, 'Classical': 151, 'New Age': 124, 'Heavy Metal': 119, 'Metal': 86}


Top ranking for 2020
    {'Pop': 563, 'French Pop': 505, 'Soundtrack': 503, 'Dance': 238, 'Classical': 229, 'New Age': 166, 'Rock': 119, 'Alternative': 110, 'Electronic': 71, 'Singer/Songwriter': 65}




So now that we looked at the top ranked, let's look at the bottom ones....

In [207]:
query_type = 'rating'
query_values = ['DISLIKE']

list_top_ranked(df_visualization, 'Genres', 5, [2016, 2017, 2018, 2019, 2020], query_type, query_values)

Top ranking for 2016
    {'Hip Hop/Rap': 6, 'Reggae': 2, 'French Pop': 1, 'World': 1, 'Rock': 0}


Top ranking for 2017
    {'Electronic': 7, 'Pop': 4, 'French Pop': 3, 'Hip Hop/Rap': 1, 'R&B/Soul': 1}


Top ranking for 2018
    {'Hip Hop/Rap': 14, 'French Pop': 7, 'R&B/Soul': 4, 'Soundtrack': 3, 'Alternative': 2}


Top ranking for 2019
    {'Hip Hop/Rap': 15, 'R&B/Soul': 4, 'French Pop': 3, 'Pop': 2, 'Dance': 2}


Top ranking for 2020
    {'Dance': 8, 'French Pop': 5, 'Pop': 3, 'Electronic': 3, 'Hip Hop/Rap': 2}




In [208]:
query_type = 'rating'
query_values = ['DISLIKE']

list_top_ranked(df_visualization, 'Artist', 5, [2016, 2017, 2018, 2019, 2020], query_type, query_values)

Top ranking for 2016
    {'Rilès': 5, 'Yaniss Odua': 2, 'Colonel Reyel': 1, 'Kanye West': 1, 'Kendji Girac': 1}


Top ranking for 2017
    {'Eugénie': 4, 'Logan Paul': 2, 'Lisandro Cuxi': 2, 'Tabitha Nauser': 2, 'Mathias Thorsen': 2}


Top ranking for 2018
    {'Ridsa': 4, 'Kanye West': 4, 'Arielle': 3, 'Svinkels': 2, 'Jemaine Clement': 2}


Top ranking for 2019
    {'Soprano': 4, 'MA2X': 3, 'Alma': 2, 'Kanye West': 2, 'Aayite': 2}


Top ranking for 2020
    {'Danny Avila': 5, 'M. Pokora': 2, 'Joy Club': 2, 'twoloud': 2, 'HUGEL': 2}




I actually don't even know these artists....

Alright, so now let's explore one more things before we move on to the next angle of analysis: whether there is a correlation between the source of a song, and whether we liked it or not. 

These are actually going to be simple pie charts, that will give the distribution of how the song was found, depending on the filters we will apply on the data to plot.

In [241]:
query_type = 'rating'
query_values = ['LOVE']

render_sunburst_plot(df_visualization, 'Track_origin', [2016, 2017, 2018, 2019, 2020], query_type, query_values)

In [242]:
query_type = ''
query_values = []

render_sunburst_plot(df_visualization, 'Track_origin', [2016, 2017, 2018, 2019, 2020], query_type, query_values)

In [ ]:
# plot the count of songs per genre for different years

fig = make_subplots(rows=1, cols=1, y_title='Number of tracks listened to')

fig.add_trace(
    go.Bar(name='2016',
           x=[*genres_count_dict_sorted.keys()],
           y=[*genres_count_dict_sorted.values()],
           marker_color='rgb(49, 104, 142)'
    ),
    row=1, col=1
)

fig.update_layout(
    title='Distribution of number of tracks listened to per genre for different years',
    height=800
)
fig.update_xaxes(matches='x')

fig.show()

In [ ]:
ig = go.Figure(data=[
    go.Bar(name='2016',
           x=df_visualization[df_visualization['Play_Year']==2016]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2016]['Play_Month'].value_counts(),
           marker_color='rgb(253, 231, 37)'
    ),
    go.Bar(name='2017',
           x=df_visualization[df_visualization['Play_Year']==2017]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2017]['Play_Month'].value_counts(),
           marker_color='rgb(68, 1, 84)'
    ),
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2018]['Play_Month'].value_counts(),
           marker_color='rgb(49, 104, 142)'
    ),
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2019]['Play_Month'].value_counts(),
           marker_color='rgb(31, 158, 137)'
    ),
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_Month'].unique(),
           y=df_visualization[df_visualization['Play_Year']==2020]['Play_Month'].value_counts(),
           marker_color='rgb(180, 222, 44)'

In [ ]:
fig.add_trace(
    go.Bar(name='2018',
           x=df_visualization[df_visualization['Play_Year']==2018]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2018]['Play_HOD_Local_Time']),
           marker_color='rgb(49, 104, 142)'
    ),
    row=3, col=1
)

fig.add_trace(
    go.Bar(name='2019',
           x=df_visualization[df_visualization['Play_Year']==2019]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2019]['Play_HOD_Local_Time']),
           marker_color='rgb(31, 158, 137)'
    ),
    row=4, col=1
)

fig.add_trace(
    go.Bar(name='2020',
           x=df_visualization[df_visualization['Play_Year']==2020]['Play_HOD_Local_Time'].unique(),
           y=compute_ratio_songs(df_visualization[df_visualization['Play_Year']==2020]['Play_HOD_Local_Time']),
           marker_color='rgb(180, 222, 44)'
    ),
    row=5, col=1
)



### Listening habits

Now let's move to our last angle of analysis, that concerns listening habits.

So here we will try to figure out:
- how songs are usually found (i.e what is the track oririn)
- where songs in the library come from (we are trying to see if the suggestions are usually relevant)
- what is the ratio of songs skipped, if there is a link between its genre, its origin and the fact that it was skipped?


In [ ]:

fig = go.Figure(go.Histogram2d(
        y=filtered_df['Play_DOM'],
        x=filtered_df['Play_Month'],
        autobiny=False,
        ybins=dict(start=0.5, end=31.5, size=-1),
        autobinx=False,
        xbins=dict(start=0.5, end=12.5, size=1),
        z=filtered_df['Play_duration_in_minutes'],
        histfunc="sum",
    ))

fig.update_layout(
    title='Heat map of the play duration in minutes for each day - 2018',
    xaxis=dict(
        tickangle = -45,
        tickmode = 'array',
        tickvals = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12],
        ticktext = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
    ),
)


fig.show()

In [ ]:
# Timeline per year 

#Play Year
fig = go.Figure(data=[
    go.Bar(name='2016', x=['2016', '2017', '2018', '2019', '2020'], y=df_combined.groupby(['Play Year'])['Play Year'].count())
])
fig.update_layout(barmode='group', title='Count fo songs listened to per month of the year, breakdown per year',
                  yaxis=dict(title="Count of songs"),
                  xaxis=dict(title="Month of the year"))
fig.show()




In [ ]:
#Play Month	Play DOM	Play DOW	Play HOD

months = df_combined['Play Month']
months_labels = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']



In [ ]:
fig = go.Figure(data=[
    go.Bar(name='2016', x=months, y=df_combined[df_combined['Play Year']=='2016']['Play Month'].value_counts()),
    go.Bar(name='2017', x=months, y=df_combined[df_combined['Play Year']=='2017']['Play Month'].value_counts()),
    go.Bar(name='2018', x=months, y=df_combined[df_combined['Play Year']=='2018']['Play Month'].value_counts()),
    go.Bar(name='2019', x=months, y=df_combined[df_combined['Play Year']=='2019']['Play Month'].value_counts()),
    go.Bar(name='2020', x=months, y=df_combined[df_combined['Play Year']=='2020']['Play Month'].value_counts())
])





fig = go.Figure()
fig.add_trace(go.Scatter(x=df_combined[df_combined['Play Year']=='2016']['Play Month'], 
                         y=df_combined[df_combined['Play Year']=='2016'].count(),
                         mode='markers',
                         name='2016'))
fig.add_trace(go.Scatter(x=df_combined[df_combined['Play Year']=='2017']['Play Month'], 
                         y=df_combined[df_combined['Play Year']=='2017'].count(),
                         mode='markers',
                         name='2017'))
fig.add_trace(go.Scatter(x=df_combined[df_combined['Play Year']=='2018']['Play Month'], 
                         y=df_combined[df_combined['Play Year']=='2018'].count(),
                         mode='markers',
                         name='2018'))
fig.add_trace(go.Scatter(x=df_combined[df_combined['Play Year']=='2019']['Play Month'], 
                         y=df_combined[df_combined['Play Year']=='2019'].count(),
                         mode='markers',
                         name='2019'))
fig.add_trace(go.Scatter(x=df_combined[df_combined['Play Year']=='2020']['Play Month'], 
                         y=df_combined[df_combined['Play Year']=='2020'].count(),
                         mode='markers',
                         name='2020'))
fig.show()

In [ ]:
ge=['giraffes', 'orangutans', 'monkeys']

fig = go.Figure(data=[
    go.Bar(name='SF Zoo', x=animals, y=[20, 14, 23]),
    go.Bar(name='LA Zoo', x=animals, y=[12, 18, 29])
])
# Change the bar mode
fig.update_layout(barmode='group')
fig.show()

- genres liked/disliked
- main genres in library
- Count of songs per year/month/dow/dom/hod
- Listening time per day/week/month
- Ranking of artists, genre, album per year, trends over the year (or per period of time, possibility to select to/from date)
- ratio of songs skipped
- Count aggregation per week or month
- Comparison of songs listened to vs when they were released
- Life cycle of a song (listened to for a long period, vs short period)
- Variation calculation with previous year/month/week stats
- Genre depending on the moment of the year/week/day
- Total minutes played and a comparison with how much time it represents in my life

In [ ]:

likes_dislikes_df

- Songs, genre liked/disliked 

In [ ]:
parsed_string = string.encode('utf-8')
regex = r"(\w|\s)*"
        matches = re.finditer(regex, parsed_string, re.DOTALL)
        uniform_string = ''
        for matchNum, match in enumerate(matches):
            matchNum = matchNum + 1
            uniform_string = uniform_string + match.group()

In [ ]:
increment = 0
track_instance_dict = {}
artist_tracks_titles = {}
items_not_matched = {'library_tracks':[], 'identifier_info':[],
                     'play_activity':[], 'likes_dislikes':[]}

# First, we build our tracks instances using the library tracks dataframe
for index, row in library_tracks_info_df.iterrows():
    if str(row['Title']) != 'nan':
        title = row['Title']
        if str(row['Artist']) != 'nan':
            artist = row['Artist']
        else:
            artist = 'No Artist'
        
        title_artist = concat_title_artist(title, artist)
        if title_artist not in track_instance_dict.keys():
            #we instantiate the Track object
            track_instance = instantiate_track(title, artist)
            update_track_from_library(track_instance, index, row)

            #we update the dictionary that keeps track of our instances, and increment
            track_instance_dict[title_artist] = track_instance
            increment+=1
        else:
            update_track_from_library(track_instance, index, row)
            

        #we update the artist/track names dictionnary
        if row['Artist'] not in artist_tracks_titles:
            artist_tracks_titles[artist]=[]
        if row['Title'] not in artist_tracks_titles[artist]:
            artist_tracks_titles[artist].append(title)
    else:
        items_not_matched['library_tracks'].append(index)


Automate the analysis and allow upload of any file
Possibility to choose which year for the report (single year, from/to)
